In [2]:


import numpy as np
import matplotlib.pyplot as plt
from ipywidgets import FloatSlider, IntSlider, Button, VBox, Layout, HBox, HTML
from IPython.display import display, HTML as DisplayHTML, clear_output
import random
from matplotlib import animation

# -----------------------------
# 🎨 Elegant UI Setup
# -----------------------------
title_html = HTML(
    "<h1 style='color:#1565C0; text-align:center; font-family:Trebuchet MS;'>🏝️ Treasure Island Adventure</h1>"
)
subtitle_html = HTML(
    "<p style='color:#444; text-align:center; font-size:16px; margin-top:-10px;'>Explore the island, collect treasures, and survive the journey!</p>"
)

prob_slider = FloatSlider(value=0.3, min=0.1, max=0.9, step=0.1, description="💰 Treasure %", layout=Layout(width='500px'))
steps_slider = IntSlider(value=50, min=10, max=200, step=10, description="🚶 Steps", layout=Layout(width='500px'))
energy_slider = IntSlider(value=150, min=50, max=300, step=10, description="⚡ Energy", layout=Layout(width='500px'))
boosters_slider = IntSlider(value=10, min=0, max=30, step=1, description="🎁 Boosters", layout=Layout(width='500px'))
start_button = Button(description="🚀 Start Adventure", button_style="success", layout=Layout(width='300px', height='60px', margin='20px auto'))

ui_box = VBox([
    title_html,
    subtitle_html,
    VBox([prob_slider, steps_slider, energy_slider, boosters_slider],
         layout=Layout(padding='10px', border='2px solid #90CAF9',
                       border_radius='15px', background_color='#E3F2FD', width='550px', margin='0 auto')),
    HBox([start_button], layout=Layout(justify_content='center')),
], layout=Layout(align_items='center'))
display(ui_box)

# -----------------------------
# 🧭 Adventure Logic
# -----------------------------
def adventure_frames(prob, steps, energy, boosters_count):
    size = 50
    island = np.random.rand(size, size) < prob
    explored = np.zeros((size, size), dtype=bool)
    player_pos = (random.randint(0,size-1), random.randint(0,size-1))
    treasures_found = 0

    boosters = np.zeros((size,size), dtype=bool)
    for _ in range(boosters_count):
        x,y = random.randint(0,size-1), random.randint(0,size-1)
        boosters[x,y] = True

    frames = []
    ran_out_of_energy = False
    trail = []

    for s in range(steps):
        i,j = player_pos
        explored[i,j] = True
        trail.append((i,j))
        if len(trail) > 5:
            trail.pop(0)

        if island[i,j]:
            treasures_found +=1
            island[i,j] = False

        if boosters[i,j]:
            energy += 10
            boosters[i,j] = False
            boosters_count -= 1

        energy -= 3
        if energy <=0:
            energy = 0
            ran_out_of_energy = True
            frames.append((island.copy(), player_pos, explored.copy(), boosters.copy(),
                           s+1, treasures_found, energy, boosters_count, trail.copy(),
                           "💀 You ran out of energy!"))
            break

        di,dj = random.choice([(1,0),(-1,0),(0,1),(0,-1)])
        new_i,new_j = max(0,min(size-1,i+di)), max(0,min(size-1,j+dj))
        player_pos = (new_i,new_j)

        frames.append((island.copy(), player_pos, explored.copy(), boosters.copy(),
                       s+1, treasures_found, energy, boosters_count, trail.copy(), None))

    if ran_out_of_energy:
        for remaining in range(s+1, steps):
            frames.append((island.copy(), player_pos, explored.copy(), boosters.copy(),
                           remaining+1, treasures_found, 0, boosters_count, trail.copy(),
                           "💀 You ran out of energy!"))
    else:
        frames.append((island.copy(), player_pos, explored.copy(), boosters.copy(),
                       steps, treasures_found, energy, boosters_count, trail.copy(),
                       f"🎉 Adventure Complete! Treasures Collected: {treasures_found}"))
    return frames

# -----------------------------
# 🌀 Animation with Circles
# -----------------------------
def run_animation(prob, steps, energy, boosters_count):
    frames = adventure_frames(prob, steps, energy, boosters_count)
    size = 50
    fig, ax = plt.subplots(figsize=(8,8))
    plt.close(fig)

    colors = {
        'sea': '#aee7ff',
        'land': '#b6e3b4',
        'treasure1': '#ffd84d',
        'treasure2': '#fff07a',
        'booster': '#b094ff',
        'player': '#1565C0',
        'trail': '#90CAF9'
    }

    def animate(k):
        ax.clear()
        island, player_pos, explored, boosters, step, treasures, energy_now, boosters_left, trail, msg = frames[k]
        ax.set_facecolor('#d4f4ff')
        ax.set_xlim(0, size)
        ax.set_ylim(0, size)
        ax.set_xticks([])
        ax.set_yticks([])

        # Plot explored land
        ex_i, ex_j = np.where(explored)
        ax.scatter(ex_j, size - np.array(ex_i), c=colors['land'], s=40, alpha=0.7)

        # Plot treasures with sparkle effect ✨
        tr_i, tr_j = np.where(island)
        if (k // 3) % 2 == 0:
            ax.scatter(tr_j, size - np.array(tr_i), c=colors['treasure1'], s=60, alpha=0.9, edgecolors='gold', linewidths=1)
        else:
            ax.scatter(tr_j, size - np.array(tr_i), c=colors['treasure2'], s=60, alpha=0.9, edgecolors='white', linewidths=1)

        # Plot boosters
        b_i, b_j = np.where(boosters)
        ax.scatter(b_j, size - np.array(b_i), c=colors['booster'], s=55, alpha=0.8, edgecolors='violet')

        # Plot player trail (fade effect)
        for idx, (ti, tj) in enumerate(trail[:-1]):
            ax.scatter(tj, size - ti, c=colors['trail'], s=40, alpha=0.2 + 0.15*idx)

        # Player as big blue circle 🧍‍♂️
        pi, pj = player_pos
        ax.scatter(pj, size - pi, c=colors['player'], s=150, edgecolors='white', linewidths=2, alpha=0.95)

        ax.set_title("🌴 Exploring Treasure Island", fontsize=16, fontweight='bold', pad=20, color="#0D47A1")
        ax.text(0, size + 2,
                f"Step: {step}/{steps} | 💰 Treasures: {treasures} | ⚡ Energy: {energy_now} | 🎁 Boosters: {boosters_left}",
                fontsize=12, color='#004d40', fontweight='bold', ha='left')
        if msg:
            ax.text(size/2, -2, msg, fontsize=13, color='red', ha='center', va='top', fontweight='bold')

    anim = animation.FuncAnimation(fig, animate, frames=len(frames), interval=180)
    return DisplayHTML(anim.to_jshtml())

# -----------------------------
# Button Click
# -----------------------------
def on_start(b):
    clear_output(wait=True)
    display(ui_box)
    anim_html = run_animation(prob_slider.value, steps_slider.value, energy_slider.value, boosters_slider.value)
    display(anim_html)

    frames = adventure_frames(prob_slider.value, steps_slider.value, energy_slider.value, boosters_slider.value)
    last_frame = frames[-1]
    final_msg = last_frame[-1]
    if final_msg is None:
        treasures_collected = last_frame[5]
        final_msg = f"🎉 Adventure Complete! Treasures Collected: {treasures_collected}"

    display(DisplayHTML(f"<h3 style='color:#2E7D32; text-align:center; font-family:Trebuchet MS;'>{final_msg}</h3>"))

start_button.on_click(on_start)

/tmp/ipython-input-1777879534.py:155: UserWarning: Glyph 127796 (\N{PALM TREE}) missing from font(s) DejaVu Sans.
  return DisplayHTML(anim.to_jshtml())
/tmp/ipython-input-1777879534.py:155: UserWarning: Glyph 128176 (\N{MONEY BAG}) missing from font(s) DejaVu Sans.
  return DisplayHTML(anim.to_jshtml())
/tmp/ipython-input-1777879534.py:155: UserWarning: Glyph 127873 (\N{WRAPPED PRESENT}) missing from font(s) DejaVu Sans.
  return DisplayHTML(anim.to_jshtml())
/tmp/ipython-input-1777879534.py:155: UserWarning: Glyph 128128 (\N{SKULL}) missing from font(s) DejaVu Sans.
  return DisplayHTML(anim.to_jshtml())
